In [1]:
import pfv_utils.utils as pu
import vision.data.proto.annotated_image_pb2
import vision.data.proto.oriented_bounding_box_annotation_extension_pb2
import vision.data.tools.fiducial_annotator.fiducial_annotator_pb2
import tensorflow as tf
import numpy as np

In [2]:
reload(pu)

<module 'pfv_utils.utils' from 'pfv_utils/utils.py'>

In [3]:
net = pu.BikeOrientationNet()

In [4]:
bike_lmdbs_dir = '/mnt/sun-pcs01/praveen/pfv_bikes/train_lmdbs/'
bike_lmdb_paths = pu.get_sorted_lmdb_paths_in_dir(bike_lmdbs_dir)

In [5]:
bike_lmdbs = [pu.LMDBIterator(f) for f in bike_lmdb_paths]

In [6]:
bike_ai = vision.data.proto.annotated_image_pb2.AnnotatedImage()
bike_ai.ParseFromString(bike_lmdbs[8].kv_pair[1])

17995

In [7]:
pu.get_bike_gt_ori_idx_from_ai(bike_ai)

8

In [8]:
import matplotlib.pyplot as plt

In [9]:
%matplotlib inline

In [10]:
batch_size = 1

In [11]:
import time

In [12]:
reload(pu)

<module 'pfv_utils.utils' from 'pfv_utils/utils.py'>

In [13]:
train_step = tf.train.AdamOptimizer(1e-4).minimize(net.loss)

In [14]:
sess = tf.Session()
sess.run(tf.global_variables_initializer())
iter = 0


In [19]:
while iter < 200000:
    start = time.time()
    # Compose batch from extent_lmdbs.
    batch_ims = []
    full_batch_size = batch_size* (len(bike_lmdbs))
    batch_bike_gts = np.zeros(full_batch_size,dtype=np.int32)
    
    batch_item_idx = -1
    for bike_lmdb_idx, bike_lmdb in enumerate(bike_lmdbs):
        for i in range(0,batch_size):
            batch_item_idx +=1
            ai = vision.data.proto.annotated_image_pb2.AnnotatedImage()
            ai.ParseFromString(bike_lmdb.kv_pair[1])
            bike_lmdb.next()
            
            batch_ims.append(pu.get_image_from_ai(ai))
            batch_bike_gts[batch_item_idx] = pu.get_bike_gt_ori_idx_from_ai(ai)
            assert (bike_lmdb_idx == batch_bike_gts[batch_item_idx])
                  

    normalized_batch_ims = pu.normalize_ims(np.array(batch_ims))
    end = time.time()
    loss, _ = sess.run([net.loss, train_step], feed_dict={net.x: normalized_batch_ims,
                                          net.y: batch_bike_gts
                                                              })
    step_end = time.time()

    assert(loss.shape == ())
    if iter % 1000 == 0:
        print 'On iter: %d; loss: %0.2f step time: %f' % (iter, loss, step_end-end)

            
    iter+=1
    
    

On iter: 36000; loss: 7.78 step time: 0.013983
On iter: 37000; loss: 7.19 step time: 0.014027
On iter: 38000; loss: 9.60 step time: 0.014020
On iter: 39000; loss: 7.21 step time: 0.013925
On iter: 40000; loss: 20.16 step time: 0.014069
On iter: 41000; loss: 9.59 step time: 0.014169
On iter: 42000; loss: 11.89 step time: 0.014078
On iter: 43000; loss: 7.90 step time: 0.013858
On iter: 44000; loss: 5.89 step time: 0.014132
On iter: 45000; loss: 6.98 step time: 0.013736
On iter: 46000; loss: 7.28 step time: 0.014437
On iter: 47000; loss: 8.45 step time: 0.014125
On iter: 48000; loss: 6.50 step time: 0.014340
On iter: 49000; loss: 14.09 step time: 0.014063
On iter: 50000; loss: 14.03 step time: 0.014055
On iter: 51000; loss: 7.48 step time: 0.013711
On iter: 52000; loss: 11.27 step time: 0.013791
On iter: 53000; loss: 10.71 step time: 0.013737
On iter: 54000; loss: 8.11 step time: 0.013767
On iter: 55000; loss: 13.18 step time: 0.014328
On iter: 56000; loss: 7.40 step time: 0.014521
On ite

In [16]:
iter

35403

In [17]:
net.x

<tf.Tensor 'input:0' shape=(?, 96, 96, 3) dtype=float32>

In [20]:
graphdef = sess.graph_def
frozen_graph = tf.graph_util.convert_variables_to_constants(sess, graphdef, ["output"])
converted_graph_def= tf.graph_util.remove_training_nodes(frozen_graph)
tf.train.write_graph(converted_graph_def, "/mnt/nautilus_rw/praveen/", "bike_ori_model.pb", as_text=False)

INFO:tensorflow:Froze 12 variables.
Converted 12 variables to const ops.


'/mnt/nautilus_rw/praveen/bike_ori_model.pb'

In [ ]:
#with open('/home/praveen/bike_ori_model.pb', 'wb') as of:
#    of.write(sess.graph_def.SerializeToString())

In [ ]:
x=1

In [ ]:
%matplotlib inline

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
normalized_batch_ims.shape

In [ ]:
pred = sess.run([net.output_logits], {net.x: normalized_batch_ims})[0]
arg_preds = np.argmax(pred, 1)

In [ ]:
plt.figure(figsize=(10,10))
for i,im in enumerate(normalized_batch_ims):
    plt.subplot(3,3,i+1)
    plt.imshow( im + 0.5);
    plt.title('i: %d pred: %d' % (i, arg_preds[i]))